In [1]:
from __future__ import absolute_import, division, print_function

# Import TensorFlow >= 1.10 and enable eager execution
import tensorflow as tf

tf.enable_eager_execution()

from matplotlib import font_manager, rc

rc('font', family='AppleGothic') #for mac

import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split
from tensorflow import keras
from tensorflow.keras.preprocessing.sequence import pad_sequences

from pprint import pprint
import numpy as np
import os

print(tf.__version__)

1.14.0


In [95]:
import pandas as pd
df = pd.read_json("moviedata2.json")

In [96]:
import re
df.movie_summary = df.movie_summary.apply(lambda x: str(x))
df.movie_summary = df.movie_summary.apply(lambda x: re.sub("[^A-Za-z. 0-9]", '', x))
df.movie_synopsis = df.movie_synopsis.apply(lambda x : str(x))
df.movie_synopsis = df.movie_synopsis.apply(lambda x : re.sub('[^A-Za-z. 0-9]', '', x))
df.movie_tagline = df.movie_tagline.apply(lambda x: str(x))



In [97]:
tl = list(df["movie_tagline"])
tl = [" ".join([ j for j in eval(i) if j != "\n"]).strip() for i in tl]

In [100]:
df.movie_tagline = tl
tl[0]

'The Next Chapter'

In [102]:
df.movie_tagline = df.movie_tagline.apply(lambda x: re.sub('[^A-Za-z. 0-9]', '', x))

In [123]:
sources = [['I', 'feel', 'hungry'],
     ['tensorflow', 'is', 'very', 'difficult'],
     ['tensorflow', 'is', 'a', 'framework', 'for', 'deep', 'learning'],
     ['tensorflow', 'is', 'very', 'fast', 'changing']]
targets = [['나는', '배가', '고프다'],
           ['텐서플로우는', '매우', '어렵다'],
           ['텐서플로우는', '딥러닝을', '위한', '프레임워크이다'],
           ['텐서플로우는', '매우', '빠르게', '변화한다']]

In [62]:
sources[0]

['I', 'feel', 'hungry']

In [77]:
#sources = [i.split() for i in df['movie_summary']]

def lem(summary):

    tokens = word_tokenize(summary)
    porter = PorterStemmer()
    stems = [porter.stem(t) for t in tokens]
    stopwords = nltk.corpus.stopwords.words('english')
    words = [w for w in stems if w.lower() not in stopwords]
    s = list(set(words))
        
    return s
df['movie_summary'] = df['movie_summary'].apply(lem)

In [142]:
sources = [i.split() for i in df['movie_summary']]
targets = [i.split() for i in df['movie_tagline']]

AttributeError: 'list' object has no attribute 'split'

# sources를 stemming해야함 하지만 어떻게?

In [154]:
r1 = re.compile(r"[^A-Za-z. 0-9]")
ts_vocab = [r1.sub("",j).lower() for i in sources for j in i ]
# s_vocab = list(set(sum(sources, [])))
s_vocab = list(set(ts_vocab))
s_vocab.sort()
s_vocab.pop(0) #0번째에 있던 공백 없앰

'.'

In [140]:
source2idx = {word : idx for idx, word in enumerate(s_vocab)}
idx2source = {idx : word for idx, word in enumerate(s_vocab)}

pprint(source2idx)


{'a': 0,
 'aa': 1,
 'aaa': 2,
 'aabasaheb': 3,
 'aabasahebs': 4,
 'aabasahebwhen': 5,
 'aachen': 6,
 'aadayen': 7,
 'aadhavan': 8,
 'aadhi': 9,
 'aadi': 10,
 'aadith': 11,
 'aadityan': 12,
 'aadmi': 13,
 'aage': 14,
 'aahe': 15,
 'aai': 16,
 'aaisa': 17,
 'aaisi': 18,
 'aaj': 19,
 'aajker': 20,
 'aakash': 21,
 'aakasha': 22,
 'aakhri': 23,
 'aala': 24,
 'aalam': 25,
 'aalavandhar': 26,
 'aalborg': 27,
 'aalia': 28,
 'aalias': 29,
 'aalo': 30,
 'aami': 31,
 'aamion': 32,
 'aamir': 33,
 'aamirs': 34,
 'aana': 35,
 'aap': 36,
 'aarajeet': 37,
 'aarathy': 38,
 'aarav': 39,
 'aardvark': 40,
 'aarhus': 41,
 'aarilirunthu': 42,
 'aarno': 43,
 'aarohanam': 44,
 'aaron': 45,
 'aaronnow': 46,
 'aarons': 47,
 'aaronson': 48,
 'aarop': 49,
 'aarp': 50,
 'aarthy': 51,
 'aarti': 52,
 'aartiand': 53,
 'aartis': 54,
 'aarun': 55,
 'aarushi': 56,
 'aaryan': 57,
 'aaryans': 58,
 'aas': 59,
 'aasen': 60,
 'aasha': 61,
 'aashiq': 62,
 'aashish': 63,
 'aashram': 64,
 'aasif': 65,
 'aasman': 66,
 'aasponser

 'actioner': 742,
 'actionfilled': 743,
 'actionfranchise': 744,
 'actionhorrorcomedy': 745,
 'actionman': 746,
 'actionmystery': 747,
 'actionoriented': 748,
 'actionpacked': 749,
 'actions': 750,
 'actionspermanently': 751,
 'actionspythriller': 752,
 'actionsreactions': 753,
 'actionthe': 754,
 'actionthriller': 755,
 'actionthrillers': 756,
 'actitud': 757,
 'activate': 758,
 'activated': 759,
 'activates': 760,
 'activating': 761,
 'activation': 762,
 'active': 763,
 'actively': 764,
 'activision': 765,
 'activism': 766,
 'activist': 767,
 'activistcomedian': 768,
 'activists': 769,
 'activites': 770,
 'activities': 771,
 'activitiesand': 772,
 'activitiesbalwant': 773,
 'activitiesfinding': 774,
 'activitiesor': 775,
 'activitiesthey': 776,
 'activity': 777,
 'activityand': 778,
 'actor': 779,
 'actorboyfriend': 780,
 'actorcomedian': 781,
 'actordirector': 782,
 'actoreditor': 783,
 'actorfilmmaker': 784,
 'actorhustler': 785,
 'actormanager': 786,
 'actorranvir': 787,
 'actorra

 'agravating': 1619,
 'agredido': 1620,
 'agree': 1621,
 'agreeable': 1622,
 'agreed': 1623,
 'agreeing': 1624,
 'agreement': 1625,
 'agreements': 1626,
 'agrees': 1627,
 'agreesthe': 1628,
 'agress': 1629,
 'agressive': 1630,
 'agressively': 1631,
 'agressors': 1632,
 'agricultural': 1633,
 'agriculturalists': 1634,
 'agriculture': 1635,
 'agricultures': 1636,
 'agriculturist': 1637,
 'agrigentum': 1638,
 'agrippa': 1639,
 'agrippina': 1640,
 'agrobusiness': 1641,
 'agron': 1642,
 'agronomist': 1643,
 'aground': 1644,
 'agua': 1645,
 'aguardan': 1646,
 'aguero': 1647,
 'aguilar': 1648,
 'aguinaga': 1649,
 'aguirre': 1650,
 'aguirres': 1651,
 'agumbe': 1652,
 'agung': 1653,
 'agureeva': 1654,
 'aguri': 1655,
 'agus': 1656,
 'agusti': 1657,
 'agustin': 1658,
 'agustina': 1659,
 'agustn': 1660,
 'agutter': 1661,
 'ah': 1662,
 'ahab': 1663,
 'ahabs': 1664,
 'ahad': 1665,
 'ahana': 1666,
 'ahandsomethis': 1667,
 'ahao': 1668,
 'ahare': 1669,
 'ahasan': 1670,
 'ahaunting': 1671,
 'ahching':

 'aldermenwives': 2180,
 'aldersimspor': 2181,
 'aldi': 2182,
 'aldjerias': 2183,
 'aldo': 2184,
 'aldonza': 2185,
 'aldos': 2186,
 'aldous': 2187,
 'aldouss': 2188,
 'aldrich': 2189,
 'aldridge': 2190,
 'aldrin': 2191,
 'aldrovandi': 2192,
 'aldy': 2193,
 'ale': 2194,
 'aleander': 2195,
 'alec': 2196,
 'alecia': 2197,
 'alecs': 2198,
 'alecu': 2199,
 'aleen': 2200,
 'alegra': 2201,
 'alegras': 2202,
 'alegre': 2203,
 'alegria': 2204,
 'aleichem': 2205,
 'aleichems': 2206,
 'aleinn': 2207,
 'aleister': 2208,
 'aleisters': 2209,
 'alejandra': 2210,
 'alejandre': 2211,
 'alejandro': 2212,
 'alejar': 2213,
 'alejo': 2214,
 'alejos': 2215,
 'alek': 2216,
 'alekhya': 2217,
 'alekos': 2218,
 'aleks': 2219,
 'aleksa': 2220,
 'aleksandar': 2221,
 'aleksander': 2222,
 'aleksandr': 2223,
 'aleksandra': 2224,
 'aleksandrov': 2225,
 'aleksandrowna': 2226,
 'aleksandrs': 2227,
 'aleksei': 2228,
 'aleksey': 2229,
 'aleksi': 2230,
 'aleman': 2231,
 'alemi': 2232,
 'alen': 2233,
 'alena': 2234,
 'alen

 'amirchand': 3136,
 'amirs': 3137,
 'amis': 3138,
 'amish': 3139,
 'amisha': 3140,
 'amishlike': 3141,
 'amisom': 3142,
 'amiss': 3143,
 'amistad': 3144,
 'amit': 3145,
 'amita': 3146,
 'amitabh': 3147,
 'amitabha': 3148,
 'amitand': 3149,
 'amitav': 3150,
 'amitbut': 3151,
 'amiti': 3152,
 'amitinspector': 3153,
 'amitone': 3154,
 'amits': 3155,
 'amituanai': 3156,
 'amityash': 3157,
 'amityville': 3158,
 'amjad': 3159,
 'amlan': 3160,
 'amlia': 3161,
 'amlie': 3162,
 'amma': 3163,
 'ammai': 3164,
 'ammaji': 3165,
 'ammammagarillu': 3166,
 'amman': 3167,
 'ammann': 3168,
 'ammar': 3169,
 'ammars': 3170,
 'ammer': 3171,
 'ammo': 3172,
 'ammoniabased': 3173,
 'ammu': 3174,
 'ammukutty': 3175,
 'ammunition': 3176,
 'ammunitions': 3177,
 'ammuthe': 3178,
 'amna': 3179,
 'amnesia': 3180,
 'amnesiaafflicted': 3181,
 'amnesiac': 3182,
 'amnesiarelated': 3183,
 'amnesic': 3184,
 'amnestied': 3185,
 'amnesty': 3186,
 'amnon': 3187,
 'amoeba': 3188,
 'amoebas': 3189,
 'amok': 3190,
 'amol': 31

...

 'waveavantgarde': 104069,
 'wavelength': 104070,
 'wavelengths': 104071,
 'wavelenth': 104072,
 'wavely': 104073,
 'waveoff': 104074,
 'waver': 104075,
 'waveriding': 104076,
 'wavering': 104077,
 'waverley': 104078,
 'waverly': 104079,
 'waverlys': 104080,
 'wavers': 104081,
 'waves': 104082,
 'waveshaping': 104083,
 'waving': 104084,
 'wavish': 104085,
 'wavy': 104086,
 'waw': 104087,
 'wawa': 104088,
 'wawaian': 104089,
 'wawrzek': 104090,
 'wax': 104091,
 'waxchandlers': 104092,
 'waxened': 104093,
 'waxfigures': 104094,
 'waxing': 104095,
 'waxman': 104096,
 'waxted': 104097,
 'waxwork': 104098,
 'way': 104099,
 'wayan': 104100,
 'wayanad': 104101,
 'wayang': 104102,
 'wayborn': 104103,
 'wayburn': 104104,
 'wayburns': 104105,
 'waydowntown': 104106,
 'wayespecially': 104107,
 'wayfarer': 104108,
 'wayfarers': 104109,
 'wayhe': 104110,
 'waylaid': 104111,
 'wayland': 104112,
 'waylay': 104113,
 'waylaying': 104114,
 'waylays': 104115,
 'wayne': 104116,
 'waynebatman': 104117,
 'w

 'widemouthed': 104916,
 'widen': 104917,
 'widening': 104918,
 'widens': 104919,
 'wideopen': 104920,
 'wideopenwill': 104921,
 'wider': 104922,
 'wideranging': 104923,
 'widerberg': 104924,
 'widerstand': 104925,
 'widescreen': 104926,
 'widespread': 104927,
 'widest': 104928,
 'widhi': 104929,
 'widhis': 104930,
 'widmark': 104931,
 'widmer': 104932,
 'widmyer': 104933,
 'widow': 104934,
 'widowed': 104935,
 'widower': 104936,
 'widowered': 104937,
 'widowerreturnee': 104938,
 'widowers': 104939,
 'widowher': 104940,
 'widowhood': 104941,
 'widows': 104942,
 'widowto': 104943,
 'widowwoman': 104944,
 'wids': 104945,
 'wie': 104946,
 'wiecek': 104947,
 'wieceks': 104948,
 'wieck': 104949,
 'wied': 104950,
 'wieden': 104951,
 'wieder': 104952,
 'wieland': 104953,
 'wield': 104954,
 'wielded': 104955,
 'wielder': 104956,
 'wielding': 104957,
 'wields': 104958,
 'wien': 104959,
 'wiener': 104960,
 'wienerdog': 104961,
 'wiesbaden': 104962,
 'wiest': 104963,
 'wife': 104964,
 'wifea': 10

 'wowing': 105906,
 'wows': 105907,
 'woyzeck': 105908,
 'woyzecks': 105909,
 'wozniak': 105910,
 'wozyeck': 105911,
 'wrack': 105912,
 'wracked': 105913,
 'wrackets': 105914,
 'wracks': 105915,
 'wraith': 105916,
 'wralan': 105917,
 'wrangler': 105918,
 'wranglers': 105919,
 'wrangles': 105920,
 'wrangling': 105921,
 'wrap': 105922,
 'wrapped': 105923,
 'wrapper': 105924,
 'wrapping': 105925,
 'wraps': 105926,
 'wrath': 105927,
 'wrathful': 105928,
 'wray': 105929,
 'wreak': 105930,
 'wreake': 105931,
 'wreaked': 105932,
 'wreaking': 105933,
 'wreaks': 105934,
 'wreastler': 105935,
 'wreck': 105936,
 'wreckage': 105937,
 'wrecked': 105938,
 'wrecker': 105939,
 'wreckers': 105940,
 'wrecking': 105941,
 'wreckofaman': 105942,
 'wrecks': 105943,
 'wren': 105944,
 'wrench': 105945,
 'wrenched': 105946,
 'wrenches': 105947,
 'wrenching': 105948,
 'wrenchingly': 105949,
 'wrens': 105950,
 'wrest': 105951,
 'wresting': 105952,
 'wrestle': 105953,
 'wrestled': 105954,
 'wrestlemonsters': 1059

 'yotas': 106867,
 'yotsuya': 106868,
 'you': 106869,
 'youcef': 106870,
 'youd': 106871,
 'youderian': 106872,
 'youif': 106873,
 'youknowwhat': 106874,
 'youll': 106875,
 'younes': 106876,
 'young': 106877,
 'youngadult': 106878,
 'youngblood': 106879,
 'youngbloods': 106880,
 'youngchun': 106881,
 'younger': 106882,
 'youngerandshiftless': 106883,
 'youngers': 106884,
 'youngest': 106885,
 'youngeun': 106886,
 'youngeuns': 106887,
 'younggoo': 106888,
 'younghae': 106889,
 'younghis': 106890,
 'youngho': 106891,
 'youngjoon': 106892,
 'younglooking': 106893,
 'youngmagician': 106894,
 'youngman': 106895,
 'youngmi': 106896,
 'youngmin': 106897,
 'youngs': 106898,
 'youngsers': 106899,
 'youngshik': 106900,
 'youngshikback': 106901,
 'youngshil': 106902,
 'youngshin': 106903,
 'youngsook': 106904,
 'youngster': 106905,
 'youngsters': 106906,
 'youngsterwhile': 106907,
 'youngstown': 106908,
 'youngsun': 106909,
 'youngtimer': 106910,
 'younnan': 106911,
 'yount': 106912,
 'your': 106

 'zoologist': 107672,
 'zoologists': 107673,
 'zoology': 107674,
 'zoom': 107675,
 'zooming': 107676,
 'zooms': 107677,
 'zoos': 107678,
 'zootsuiter': 107679,
 'zorabian': 107680,
 'zoran': 107681,
 'zorans': 107682,
 'zoravar': 107683,
 'zorba': 107684,
 'zorbas': 107685,
 'zordon': 107686,
 'zorer': 107687,
 'zoret': 107688,
 'zorica': 107689,
 'zorina': 107690,
 'zoritsa': 107691,
 'zorka': 107692,
 'zorkas': 107693,
 'zorn': 107694,
 'zorns': 107695,
 'zoroark': 107696,
 'zoroastrianism': 107697,
 'zorro': 107698,
 'zosia': 107699,
 'zoubir': 107700,
 'zovek': 107701,
 'zovnig': 107702,
 'zovyot': 107703,
 'zoya': 107704,
 'zozo': 107705,
 'zpg': 107706,
 'zs': 107707,
 'zsa': 107708,
 'zschiesche': 107709,
 'zsigmond': 107710,
 'zsolt': 107711,
 'zspace': 107712,
 'ztopek': 107713,
 'zu': 107714,
 'zuaiter': 107715,
 'zubeda': 107716,
 'zubeida': 107717,
 'zubin': 107718,
 'zubiri': 107719,
 'zubov': 107720,
 'zubrin': 107721,
 'zubuk': 107722,
 'zubuks': 107723,
 'zucchini': 107

In [141]:
len(source2idx)

107799

In [86]:
# vocabulary for targets
t_vocab = list(set(sum(targets, [])))
t_vocab.sort()
t_vocab = ['<pad>', '<bos>', '<eos>'] + t_vocab
target2idx = {word : idx for idx, word in enumerate(t_vocab)}
idx2target = {idx : word for idx, word in enumerate(t_vocab)}

pprint(target2idx)

{'!': 3,
 '!!': 4,
 '!"': 5,
 '!(original': 6,
 '!)': 7,
 '!..': 8,
 '"': 9,
 '"(ORIGINAL': 10,
 '".': 11,
 '"...': 12,
 '"...I': 13,
 '"20': 14,
 '"7th': 15,
 '"A': 16,
 '"A"': 17,
 '"ADELE"': 18,
 '"ALL-AMERICAN"!': 19,
 '"Action"': 20,
 '"Adultress"!': 21,
 '"After': 22,
 '"Al': 23,
 '"Alfie"': 24,
 '"All': 25,
 '"Alone"': 26,
 '"Alone?"': 27,
 '"American': 28,
 '"Around': 29,
 '"Arsenal': 30,
 '"Autism': 31,
 '"BANDOLERO!".': 32,
 '"BEAUTIFUL': 33,
 '"BEN"': 34,
 '"BITTER': 35,
 '"BLACK': 36,
 '"BRAHAM\'S': 37,
 '"BULLDOG': 38,
 '"Baby': 39,
 '"Back-Home"': 40,
 '"Bad': 41,
 '"Ballad': 42,
 '"Bars"': 43,
 '"Because': 44,
 '"Best': 45,
 '"Big': 46,
 '"Blonde': 47,
 '"Blondie': 48,
 '"Boom': 49,
 '"Boy,': 50,
 '"Bright': 51,
 '"But': 52,
 '"Butterflies': 53,
 '"By': 54,
 '"Byejeh': 55,
 '"CAMILLE"': 56,
 '"COME': 57,
 '"CONDEMNED"...': 58,
 '"CRIME': 59,
 '"Caesar': 60,
 '"Calypso': 61,
 '"Canaris"': 62,
 '"Candy': 63,
 '"Carmen",': 64,
 '"Carnal': 65,
 '"Carry': 66,
 '"Charlotte': 6

 '(SAS)': 763,
 '(San': 764,
 '(Some': 765,
 '(Sometimes': 766,
 '(Spain': 767,
 '(Studio': 768,
 '(Swedish': 769,
 '(The': 770,
 "(There's": 771,
 '(They': 772,
 "(They're": 773,
 '(Think': 774,
 '(Thirty': 775,
 '(This': 776,
 '(Title': 777,
 '(Tomorrow': 778,
 '(Trade': 779,
 '(Turbulent': 780,
 '(U.S.': 781,
 '(UK': 782,
 '(UK)': 783,
 '(US': 784,
 '(USA': 785,
 '(USA)': 786,
 '(USA/Canada': 787,
 '(Welcome': 788,
 '(What': 789,
 '(With': 790,
 '(You': 791,
 "(You've": 792,
 '(Yusuke': 793,
 '(again)': 794,
 '(all': 795,
 '(almost)': 796,
 '(and': 797,
 '(chapter': 798,
 '(dvd)': 799,
 '(former': 800,
 '(from': 801,
 '(if': 802,
 '(instead': 803,
 '(international': 804,
 '(locksmith).': 805,
 '(newspaper': 806,
 '(noun': 807,
 '(n챈sten)': 808,
 '(oiginal': 809,
 '(original': 810,
 '(original-USA-poster-all': 811,
 '(original-ad)': 812,
 '(oriiginal': 813,
 '(poster).': 814,
 '(prigina': 815,
 '(priginal': 816,
 '(print': 817,
 '(pronounced': 818,
 "(rap'chur)": 819,
 '(re-relase-po

 'Acid,': 1499,
 'Acre)': 1500,
 'Across': 1501,
 'Act': 1502,
 'Action': 1503,
 'Action!': 1504,
 'Action!!': 1505,
 'Action,': 1506,
 'Action-Crammed': 1507,
 'Action-Packed': 1508,
 'Action.': 1509,
 'Action...': 1510,
 'Action...Stirring': 1511,
 'Action.He': 1512,
 'Action:': 1513,
 'Actions': 1514,
 'Activism': 1515,
 'Activist.': 1516,
 'Actors,': 1517,
 'Actress': 1518,
 'Acts': 1519,
 'Actual': 1520,
 'Actually': 1521,
 'Actually,': 1522,
 'Actually.': 1523,
 'Ad)': 1524,
 'Ad,': 1525,
 'Ad-': 1526,
 'Ad-Albany': 1527,
 'Ad-Aurora': 1528,
 'Ad-Daily': 1529,
 'Ad-Decorah': 1530,
 'Ad-Evening': 1531,
 'Ad-Gazette': 1532,
 'Ad-Leroy': 1533,
 'Ad-New': 1534,
 'Ad-Niagra': 1535,
 'Ad-Painesville': 1536,
 'Ad-Philadelphia': 1537,
 'Ad-Pittsburgh': 1538,
 'Ad-Queanbeyan': 1539,
 'Ad-Rocester': 1540,
 'Ad-San': 1541,
 'Ad-Silver': 1542,
 'Ad-Telegraph': 1543,
 'Ad-Telegraph-Herald,': 1544,
 'Ad-The': 1545,
 'Ad-Turtle': 1546,
 'Ad-Vancouver': 1547,
 'Ad-Winthrop': 1548,
 'Ada?': 1549,

 'BRITISH': 2173,
 'BROADWAY': 2174,
 'BROKEN': 2175,
 'BROMFIELD': 2176,
 'BRONSON': 2177,
 'BROTHERS': 2178,
 'BRUCE': 2179,
 'BRUMMEL!': 2180,
 'BRUSH-OFF...because': 2181,
 'BUCK': 2182,
 'BUG!': 2183,
 'BUGLE': 2184,
 'BUGgy': 2185,
 'BUILD': 2186,
 'BULLETS': 2187,
 'BULLETS...': 2188,
 'BUMSTEADS': 2189,
 'BURIED': 2190,
 'BURNING': 2191,
 'BURZYNSKI.': 2192,
 'BUSTER': 2193,
 'BUSTER...on': 2194,
 "BUSTIN'": 2195,
 'BUT': 2196,
 'BY': 2197,
 'Baba': 2198,
 'Baba!': 2199,
 "Babe's": 2200,
 'Babes!': 2201,
 "Babette's": 2202,
 'Babies': 2203,
 'Babu': 2204,
 'Baby': 2205,
 'Baby!': 2206,
 'Baby!"': 2207,
 'Baby,': 2208,
 'Baby...': 2209,
 'Baby?': 2210,
 'Bachelor': 2211,
 'Back': 2212,
 'Back!': 2213,
 'Back!"': 2214,
 'Back,': 2215,
 'Back-Bay': 2216,
 'Back.': 2217,
 'Back...A': 2218,
 'Backstage': 2219,
 'Bad': 2220,
 'Bad!': 2221,
 'Bad-Ass!': 2222,
 'Bad.': 2223,
 'Badasses.': 2224,
 'Baden-Wurttemburg))': 2225,
 'Badge': 2226,
 'Badge...A': 2227,
 'Badman': 2228,
 'Badmen'

 'Chapters': 3235,
 'Characters': 3236,
 'Characters...Very': 3237,
 'Charles': 3238,
 'Charles.': 3239,
 'Charleston': 3240,
 'Charleston.': 3241,
 'Charley': 3242,
 'Charlie': 3243,
 'Charlie!': 3244,
 "Charlie's": 3245,
 'Charlie.': 3246,
 'Charlie...the': 3247,
 'Charlotte."': 3248,
 'Charm': 3249,
 'Charm!': 3250,
 'Charm:': 3251,
 'Charmaine': 3252,
 'Charming': 3253,
 'Chart': 3254,
 'Chase': 3255,
 'Chased': 3256,
 'Chased!': 3257,
 'Chasing': 3258,
 'Chato': 3259,
 "Chato's": 3260,
 'Chautauqua': 3261,
 'Cheat': 3262,
 'Cheat"': 3263,
 'Cheated?': 3264,
 'Check': 3265,
 'Checks': 3266,
 'Cheech': 3267,
 'Cheer': 3268,
 'Cheerleader': 3269,
 'Cheerleaders': 3270,
 'Cheerleaders,': 3271,
 'Cherkassov,': 3272,
 'Cherokee': 3273,
 'Chevrolet.': 3274,
 'Cheyenne': 3275,
 'Chi': 3276,
 "Chiba's": 3277,
 'Chiba,': 3278,
 'Chicago': 3279,
 'Chick': 3280,
 'Chicken': 3281,
 'Chicks': 3282,
 'Chicks,': 3283,
 'Chief': 3284,
 'Chihuahua': 3285,
 'Child': 3286,
 "Child's": 3287,
 'Child,'

...

 'ruthless': 23421,
 'ruthless...': 23422,
 'ruva...': 23423,
 'rymmen...': 23424,
 'r챕ussir?': 23425,
 'r챗v챕': 23426,
 's': 23427,
 's#*%': 23428,
 'saD': 23429,
 'saarbar.': 23430,
 'sab': 23431,
 'saber': 23432,
 'sabotage...and': 23433,
 'saboteurs': 23434,
 'sacred': 23435,
 'sacred?': 23436,
 'sacrifice': 23437,
 'sacrifice,': 23438,
 'sacrifice.': 23439,
 'sacrificed': 23440,
 'sacrificed.': 23441,
 'sacrifices': 23442,
 'sacrifices!': 23443,
 'sacrifier.': 23444,
 'sad': 23445,
 'sad,': 23446,
 'saddle': 23447,
 'saddle!': 23448,
 'saddle-bum...desert': 23449,
 'saddle...and': 23450,
 'sadistic': 23451,
 'safe': 23452,
 'safe,': 23453,
 'safe.': 23454,
 'safe...': 23455,
 'safe...!': 23456,
 'safe...he': 23457,
 'safecracker,': 23458,
 'safecracker...': 23459,
 'safer)!': 23460,
 'safety': 23461,
 'saga': 23462,
 'saga.The': 23463,
 'sagas': 23464,
 'saiaku': 23465,
 'said': 23466,
 'sailed': 23467,
 'sailed!': 23468,
 'sailing': 23469,
 "sailor's": 23470,
 'sailor,': 23471,
 '

 'sivuosissa': 24086,
 'six': 24087,
 'six-gun!': 24088,
 'six-guns': 24089,
 'six-guns...': 24090,
 'six-sheet': 24091,
 'sixteen': 24092,
 'sixth': 24093,
 'sixth.': 24094,
 'sixties...': 24095,
 'size': 24096,
 'sizes': 24097,
 'sizes.': 24098,
 'sizzle': 24099,
 'sizzle?': 24100,
 'sizzling': 24101,
 'sj채lv...': 24102,
 'sj챈ldent': 24103,
 'ska': 24104,
 'skal': 24105,
 'skaml철s': 24106,
 'skatkammer': 24107,
 'skeletons,': 24108,
 'skies': 24109,
 'skies!': 24110,
 'skiing': 24111,
 'skilfully': 24112,
 'skilled': 24113,
 'skills': 24114,
 'skim': 24115,
 'skin': 24116,
 'skin,': 24117,
 'skin.': 24118,
 'skipper': 24119,
 'skirt...': 24120,
 'skitsak': 24121,
 'skop': 24122,
 'skratt': 24123,
 'skratten': 24124,
 'skridtet': 24125,
 'skuespiller': 24126,
 'skuggorna': 24127,
 'skulduggery,': 24128,
 'skulle': 24129,
 'skumspr첩jt,': 24130,
 'sky': 24131,
 "sky's": 24132,
 'sky,': 24133,
 'sky-heights': 24134,
 'sky-spy': 24135,
 'sky.': 24136,
 'sky...love': 24137,
 'skyjacker': 2

 'teachers': 25035,
 'teaches': 25036,
 'teachings': 25037,
 'team': 25038,
 'team!': 25039,
 'team...': 25040,
 'teams': 25041,
 'teamwork': 25042,
 'tear': 25043,
 'tear-apart.': 25044,
 'tearing': 25045,
 'tears': 25046,
 'tears,': 25047,
 'tears-': 25048,
 'tears.': 25049,
 'tease!': 25050,
 'teasing,': 25051,
 'technique': 25052,
 'technology': 25053,
 'teddies': 25054,
 'teed': 25055,
 'teen': 25056,
 'teen,': 25057,
 'teenage': 25058,
 'teenager': 25059,
 "teenager's": 25060,
 'teenagers': 25061,
 'teens': 25062,
 'teeth': 25063,
 'teeth!': 25064,
 'teht채v채?': 25065,
 'telephone': 25066,
 'television': 25067,
 'television.': 25068,
 'tell': 25069,
 'tell!': 25070,
 'tell,': 25071,
 'tell.': 25072,
 'tell...': 25073,
 'teller!': 25074,
 'tellers': 25075,
 'telling': 25076,
 'tells': 25077,
 'tells...it': 25078,
 'tem': 25079,
 'tem,': 25080,
 'temperament': 25081,
 'temperature...and': 25082,
 'tempest.': 25083,
 'tempestuous': 25084,
 'tempo': 25085,
 'tempo!': 25086,
 'tempt': 

 'vai': 25992,
 'valhetta.': 25993,
 'valiant': 25994,
 'valley': 25995,
 'valuable?': 25996,
 'value': 25997,
 'value!!': 25998,
 'valued,': 25999,
 'values': 26000,
 'vampire': 26001,
 'vamps': 26002,
 'van': 26003,
 'vanished': 26004,
 'vanished,': 26005,
 'vanliga': 26006,
 'var': 26007,
 'varje': 26008,
 'vas': 26009,
 'vast': 26010,
 'vast,': 26011,
 'vasta': 26012,
 'vastness': 26013,
 'vayas,': 26014,
 'vb:': 26015,
 'vegan': 26016,
 'vegetables...No': 26017,
 'vein': 26018,
 'veins': 26019,
 'veldt!': 26020,
 'velk챕': 26021,
 'vem': 26022,
 'vengeance': 26023,
 'vengeance!': 26024,
 'vengeance.': 26025,
 'vengeance...And': 26026,
 'vengeance...and': 26027,
 'vengeful': 26028,
 'venner...': 26029,
 'venom': 26030,
 'venom.': 26031,
 'venture': 26032,
 'venturing': 26033,
 'ver': 26034,
 'veramente': 26035,
 'veras': 26036,
 'verb': 26037,
 'verdadera': 26038,
 'verdict': 26039,
 'verge': 26040,
 'verheiratet': 26041,
 'veritable': 26042,
 'verkligheten': 26043,
 'verlieren,': 2

 'years,': 26741,
 'years-and': 26742,
 'years.': 26743,
 'years...': 26744,
 'years...as': 26745,
 'years.Legends': 26746,
 'years?': 26747,
 'yells': 26748,
 'yes,': 26749,
 'yes.': 26750,
 'yesterday.': 26751,
 'yet': 26752,
 'yet!': 26753,
 'yet.': 26754,
 'yet...but': 26755,
 'yet?': 26756,
 'yhdess채': 26757,
 'yogis': 26758,
 'yokub척,': 26759,
 'you': 26760,
 'you!': 26761,
 'you"': 26762,
 "you'd": 26763,
 "you'll": 26764,
 "you're": 26765,
 "you're...": 26766,
 "you'v": 26767,
 "you've": 26768,
 'you,': 26769,
 'you.': 26770,
 'you."': 26771,
 'you.(Print': 26772,
 'you...': 26773,
 'you..."': 26774,
 'you...)': 26775,
 'you...STAY': 26776,
 'you...What': 26777,
 'you...no': 26778,
 "you...you're": 26779,
 'you:': 26780,
 'you?': 26781,
 'young': 26782,
 'young,': 26783,
 'young.': 26784,
 'young...': 26785,
 "young.They're": 26786,
 'young?': 26787,
 'younger': 26788,
 'youngest': 26789,
 'your': 26790,
 'yours': 26791,
 'yours!': 26792,
 'yours.': 26793,
 'yours?': 26794,
 'y

In [87]:
len(target2idx)

26878

In [28]:
def preprocess(sequences, max_len, dic, mode = 'source'):
    assert mode in ['source', 'target'], 'source와 target 중에 선택해주세요.'
    
    if mode == 'source':
        # preprocessing for source (encoder)
        s_input = list(map(lambda sentence : [dic.get(token) for token in sentence], sequences))
        s_input = [[x for x in each_input if x] for each_input in s_input]
        s_len = list(map(lambda sentence : len(sentence), s_input))
        s_input = pad_sequences(sequences = s_input, maxlen = max_len, padding = 'post', truncating = 'post')
        return s_len, s_input
    

    elif mode == 'target':
        # preprocessing for target (decoder)
        # input
        t_input = list(map(lambda sentence : ['<bos>'] + sentence + ['<eos>'], sequences))
        t_input = [[x for x in each_input if x] for each_input in t_input]
        t_input = list(map(lambda sentence : [dic.get(token) for token in sentence], t_input))
        t_len = list(map(lambda sentence : len(sentence), t_input))
        t_input = pad_sequences(sequences = t_input, maxlen = max_len, padding = 'post', truncating = 'post')
     
        # output
        t_output = list(map(lambda sentence : sentence + ['<eos>'], sequences))
        t_output = list(map(lambda sentence : [dic.get(token) for token in sentence], t_output))
        t_output = pad_sequences(sequences = t_output, maxlen = max_len, padding = 'post', truncating = 'post')
        
        return t_len, t_input, t_output

In [29]:
# preprocessing for source
s_max_len = 10
s_len, s_input = preprocess(sequences = sources,
                            max_len = s_max_len, dic = source2idx, mode = 'source')
print(s_len, s_input)

[82, 78, 288, 0, 396, 202, 711, 365, 421, 460, 36, 569, 465, 115, 423, 198, 53, 489, 280, 449, 132, 376, 638, 487, 189, 282, 280, 220, 333, 654, 446, 287, 266, 153, 415, 555, 444, 340, 348, 112, 264, 54, 520, 259, 318, 315, 253, 133, 20, 266, 526, 291, 201, 502, 171, 495, 713, 274, 52, 466, 102, 335, 289, 707, 491, 268, 602, 126, 452, 273, 136, 609, 214, 187, 340, 552, 123, 232, 64, 268, 51, 455, 8, 379, 327, 426, 10, 85, 398, 442, 620, 151, 273, 23, 567, 46, 402, 527, 23, 584, 156, 373, 375, 721, 364, 195, 500, 205, 13, 313, 512, 348, 142, 338, 366, 131, 220, 215, 291, 216, 386, 348, 83, 422, 88, 418, 36, 347, 176, 410, 517, 194, 18, 18, 23, 21, 508, 419, 255, 206, 39, 201, 466, 534, 52, 89, 14, 130, 175, 396, 426, 618, 132, 87, 372, 828, 200, 333, 512, 321, 294, 13, 127, 371, 22, 323, 170, 174, 11, 116, 199, 609, 237, 22, 307, 98, 170, 315, 319, 603, 123, 116, 353, 570, 209, 262, 67, 266, 375, 465, 142, 239, 106, 31, 31, 277, 101, 221, 254, 280, 411, 409, 402, 299, 124, 160, 59, 215,

In [30]:
# preprocessing for target
t_max_len = 12
t_len, t_input, t_output = preprocess(sequences = targets,
                                      max_len = t_max_len, dic = target2idx, mode = 'target')
print(t_len, t_input, t_output)

[5, 5, 7, 2, 18, 5, 7, 9, 5, 20, 2, 6, 12, 2, 12, 9, 2, 5, 17, 6, 2, 5, 10, 9, 9, 9, 6, 5, 11, 5, 12, 25, 8, 8, 8, 6, 5, 2, 6, 4, 2, 2, 10, 4, 8, 5, 2, 2, 8, 26, 17, 7, 6, 8, 13, 5, 8, 11, 49, 6, 13, 7, 12, 8, 13, 10, 19, 8, 9, 6, 2, 10, 8, 15, 8, 8, 2, 6, 6, 17, 9, 8, 2, 9, 6, 8, 2, 75, 8, 35, 5, 12, 8, 2, 8, 2, 2, 9, 2, 4, 10, 10, 8, 12, 6, 12, 8, 13, 8, 8, 2, 4, 12, 22, 4, 2, 9, 7, 15, 6, 4, 7, 10, 2, 5, 23, 2, 10, 8, 10, 8, 8, 5, 7, 9, 2, 6, 10, 10, 7, 12, 8, 7, 7, 2, 2, 5, 7, 6, 27, 12, 5, 23, 7, 8, 5, 6, 5, 12, 2, 6, 6, 5, 12, 6, 10, 14, 19, 2, 2, 4, 12, 8, 7, 2, 6, 16, 6, 15, 8, 2, 8, 8, 9, 6, 5, 9, 37, 11, 2, 7, 15, 2, 2, 2, 6, 5, 4, 13, 13, 11, 20, 8, 10, 2, 11, 6, 14, 8, 7, 13, 10, 6, 12, 14, 7, 5, 9, 6, 2, 2, 7, 2, 13, 6, 6, 10, 16, 10, 14, 2, 7, 2, 9, 10, 16, 6, 2, 11, 8, 14, 6, 2, 10, 6, 13, 8, 13, 22, 8, 21, 11, 10, 23, 6, 6, 2, 5, 13, 10, 18, 6, 10, 6, 6, 6, 11, 2, 12, 5, 2, 7, 2, 8, 6, 15, 5, 7, 5, 12, 8, 9, 2, 10, 8, 8, 6, 4, 29, 9, 2, 4, 6, 2, 2, 19, 11, 5, 20, 14, 6,

In [31]:
# hyper-parameters
epochs = 100
batch_size = 4
learning_rate = .005
total_step = epochs / batch_size
buffer_size = 100
n_batch = buffer_size//batch_size
embedding_dim = 32
units = 128

# input
data = tf.data.Dataset.from_tensor_slices((s_len, s_input, t_len, t_input, t_output))
data = data.shuffle(buffer_size = buffer_size)
data = data.batch(batch_size = batch_size)
# s_mb_len, s_mb_input, t_mb_len, t_mb_input, t_mb_output = iterator.get_next()

In [32]:
data

<DatasetV1Adapter shapes: ((?,), (?, 10), (?,), (?, 12), (?, 12)), types: (tf.int32, tf.int32, tf.int32, tf.int32, tf.int32)>

In [33]:
def gru(units):
  # If you have a GPU, we recommend using CuDNNGRU(provides a 3x speedup than GRU)
  # the code automatically does that.
    if tf.test.is_gpu_available():
        return tf.keras.layers.CuDNNGRU(units, 
                                        return_sequences=True, 
                                        return_state=True, 
                                        recurrent_initializer='glorot_uniform')
    else:
        return tf.keras.layers.GRU(units, 
                                   return_sequences=True, 
                                   return_state=True, 
                                   recurrent_activation='sigmoid', 
                                   recurrent_initializer='glorot_uniform')

In [34]:
class Encoder(tf.keras.Model):
    def __init__(self, vocab_size, embedding_dim, enc_units, batch_sz):
        super(Encoder, self).__init__()
        self.batch_sz = batch_sz
        self.enc_units = enc_units
        self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
        self.gru = gru(self.enc_units)
        
    def call(self, x, hidden):
        x = self.embedding(x)
        output, state = self.gru(x, initial_state = hidden)
#         print("state: {}".format(state.shape))
#         print("output: {}".format(state.shape))
              
        return output, state
    
    def initialize_hidden_state(self):
        return tf.zeros((self.batch_sz, self.enc_units))

In [35]:
class Decoder(tf.keras.Model):
    def __init__(self, vocab_size, embedding_dim, dec_units, batch_sz):
        super(Decoder, self).__init__()
        self.batch_sz = batch_sz
        self.dec_units = dec_units
        self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
        self.gru = gru(self.dec_units)
        self.fc = tf.keras.layers.Dense(vocab_size)
        
        # used for attention
        self.W1 = tf.keras.layers.Dense(self.dec_units)
        self.W2 = tf.keras.layers.Dense(self.dec_units)
        self.V = tf.keras.layers.Dense(1)
        
    def call(self, x, hidden, enc_output):
        # enc_output shape == (batch_size, max_length, hidden_size)
        
        # hidden shape == (batch_size, hidden size)
        # hidden_with_time_axis shape == (batch_size, 1, hidden size)
        # we are doing this to perform addition to calculate the score
        hidden_with_time_axis = tf.expand_dims(hidden, 1)
        # * `score = FC(tanh(FC(EO) + FC(H)))`
        # score shape == (batch_size, max_length, 1)
        # we get 1 at the last axis because we are applying tanh(FC(EO) + FC(H)) to self.V
        score = self.V(tf.nn.tanh(self.W1(enc_output) + self.W2(hidden_with_time_axis)))
                
        #* `attention weights = softmax(score, axis = 1)`. Softmax by default is applied on the last axis but here we want to apply it on the *1st axis*, since the shape of score is *(batch_size, max_length, 1)*. `Max_length` is the length of our input. Since we are trying to assign a weight to each input, softmax should be applied on that axis.
        # attention_weights shape == (batch_size, max_length, 1)
        attention_weights = tf.nn.softmax(score, axis=1)
        
        # context_vector shape after sum == (batch_size, hidden_size)
        # * `context vector = sum(attention weights * EO, axis = 1)`. Same reason as above for choosing axis as 1.
        context_vector = attention_weights * enc_output
        context_vector = tf.reduce_sum(context_vector, axis=1)
        
        # x shape after passing through embedding == (batch_size, 1, embedding_dim)
        # * `embedding output` = The input to the decoder X is passed through an embedding layer.
        x = self.embedding(x)
        
        # x shape after concatenation == (batch_size, 1, embedding_dim + hidden_size)
        # * `merged vector = concat(embedding output, context vector)`
        x = tf.concat([tf.expand_dims(context_vector, 1), x], axis=-1)
        
        # passing the concatenated vector to the GRU
        output, state = self.gru(x)
        
        # output shape == (batch_size * 1, hidden_size)
        output = tf.reshape(output, (-1, output.shape[2]))
        
        # output shape == (batch_size * 1, vocab)
        x = self.fc(output)
        
        return x, state, attention_weights
        
    def initialize_hidden_state(self):
        return tf.zeros((self.batch_sz, self.dec_units))

In [36]:
encoder = Encoder(len(source2idx), embedding_dim, units, batch_size)
decoder = Decoder(len(target2idx), embedding_dim, units, batch_size)

def loss_function(real, pred):
    mask = 1 - np.equal(real, 0)
    loss_ = tf.nn.sparse_softmax_cross_entropy_with_logits(labels=real, logits=pred) * mask
    
#     print("real: {}".format(real))
#     print("pred: {}".format(pred))
#     print("mask: {}".format(mask))
#     print("loss: {}".format(tf.reduce_mean(loss_)))
    
    return tf.reduce_mean(loss_)

# creating optimizer
optimizer = tf.train.AdamOptimizer()

# creating check point (Object-based saving)
checkpoint_dir = './data_out/training_checkpoints'
checkpoint_prefix = os.path.join(checkpoint_dir, 'ckpt')
checkpoint = tf.train.Checkpoint(optimizer=optimizer,
                                encoder=encoder,
                                decoder=decoder)

# create writer for tensorboard
summary_writer = tf.contrib.summary.create_file_writer(logdir=checkpoint_dir)

W0930 19:47:59.557367 21676 lazy_loader.py:50] 
The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



In [ ]:
EPOCHS = 1

for epoch in range(EPOCHS):
    
    hidden = encoder.initialize_hidden_state()
    total_loss = 0
    
    for i, (s_len, s_input, t_len, t_input, t_output) in enumerate(data):
        loss = 0
        with tf.GradientTape() as tape:
            enc_output, enc_hidden = encoder(s_input, hidden)
            
            dec_hidden = enc_hidden
            
            dec_input = tf.expand_dims([target2idx['<bos>']] * batch_size, 1)
            
            #Teacher Forcing: feeding the target as the next input
            for t in range(1, t_input.shape[1]):
                predictions, dec_hidden, _ = decoder(dec_input, dec_hidden, enc_output)
                
                loss += loss_function(t_input[:, t], predictions)
            
                dec_input = tf.expand_dims(t_input[:, t], 1) #using teacher forcing
                
        batch_loss = (loss / int(t_input.shape[1]))
        
        total_loss += batch_loss
        
        variables = encoder.variables + decoder.variables
        
        gradient = tape.gradient(loss, variables)
        
        optimizer.apply_gradients(zip(gradient, variables))
        
    if epoch % 10 == 0:
        #save model every 10 epoch
        print('Epoch {} Loss {:.4f} Batch Loss {:.4f}'.format(epoch,
                                            total_loss / n_batch,
                                            batch_loss.numpy()))
        checkpoint.save(file_prefix = checkpoint_prefix)

In [ ]:
def evaluate(sentence, encoder, decoder, inp_lang, targ_lang, max_length_inp, max_length_targ):
    attention_plot = np.zeros((max_length_targ, max_length_inp))
    
#     sentence = preprocess_sentence(sentence)

    inputs = [inp_lang[i] for i in sentence.split(' ')]
    inputs = tf.keras.preprocessing.sequence.pad_sequences([inputs], maxlen=max_length_inp, padding='post')
    inputs = tf.convert_to_tensor(inputs)
    
    result = ''

    hidden = [tf.zeros((1, units))]
    enc_out, enc_hidden = encoder(inputs, hidden)

    dec_hidden = enc_hidden
    dec_input = tf.expand_dims([targ_lang['<bos>']], 0)

    for t in range(max_length_targ):
        predictions, dec_hidden, attention_weights = decoder(dec_input, dec_hidden, enc_out)
        
        # storing the attention weigths to plot later on
        attention_weights = tf.reshape(attention_weights, (-1, ))
        attention_plot[t] = attention_weights.numpy()

        predicted_id = tf.argmax(predictions[0]).numpy()

        result += idx2target[predicted_id] + ' '

        if idx2target.get(predicted_id) == '<eos>':
            return result, sentence, attention_plot
        
        # the predicted ID is fed back into the model
        dec_input = tf.expand_dims([predicted_id], 0)

    return result, sentence, attention_plot

# result, sentence, attention_plot = evaluate(sentence, encoder, decoder, source2idx, target2idx,
#                                             s_max_len, t_max_len)

In [ ]:
# function for plotting the attention weights
def plot_attention(attention, sentence, predicted_sentence):
    fig = plt.figure(figsize=(10,10))
    ax = fig.add_subplot(1, 1, 1)
    ax.matshow(attention, cmap='viridis')
    
    fontdict = {'fontsize': 14}
    
    ax.set_xticklabels([''] + sentence, fontdict=fontdict, rotation=90)
    ax.set_yticklabels([''] + predicted_sentence, fontdict=fontdict)

    plt.show()

In [ ]:
def translate(sentence, encoder, decoder, inp_lang, targ_lang, max_length_inp, max_length_targ):
    result, sentence, attention_plot = evaluate(sentence, encoder, decoder, inp_lang, targ_lang, max_length_inp, max_length_targ)
        
    print('Input: {}'.format(sentence))
    print('Predicted translation: {}'.format(result))
    
    attention_plot = attention_plot[:len(result.split(' ')), :len(sentence.split(' '))]
    plot_attention(attention_plot, sentence.split(' '), result.split(' '))

In [ ]:
#restore checkpoint

checkpoint.restore(tf.train.latest_checkpoint(checkpoint_dir))

In [ ]:
sentence = 'I feel hungry'
# sentence = 'tensorflow is a framework for deep learning'

translate(sentence, encoder, decoder, source2idx, target2idx, s_max_len, t_max_len)